<a href="https://colab.research.google.com/github/suhyeon0325/TIL/blob/main/laidd/check_inorganics.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install rdkit-pypi

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 29.4/29.4 MB 29.7 MB/s eta 0:00:00


In [2]:
import os
import pandas as pd
from rdkit import Chem

In [3]:
df = pd.read_csv("/content/drive/MyDrive/파이널/data/aqsol_actives.csv")

In [4]:
df.head()

ID                                               Name  \
0  A-3         N,N,N-trimethyloctadecan-1-aminium bromide   
1  A-4                           Benzo[cd]indol-2(1H)-one   
2  A-5                               4-chlorobenzaldehyde   
3  A-8  zinc bis[2-hydroxy-3,5-bis(1-phenylethyl)benzo...   
4  A-9  4-({4-[bis(oxiran-2-ylmethyl)amino]phenyl}meth...   

                                               InChI  \
0  InChI=1S/C21H46N.BrH/c1-5-6-7-8-9-10-11-12-13-...   
1  InChI=1S/C11H7NO/c13-11-8-5-1-3-7-4-2-6-9(12-1...   
2        InChI=1S/C7H5ClO/c8-7-3-1-6(5-9)2-4-7/h1-5H   
3  InChI=1S/2C23H22O3.Zn/c2*1-15(17-9-5-3-6-10-17...   
4  InChI=1S/C25H30N2O4/c1-5-20(26(10-22-14-28-22)...   

                      InChIKey  \
0  SZEMGTQCPRNXEG-UHFFFAOYSA-M   
1  GPYLCFQEKPUWLD-UHFFFAOYSA-N   
2  AVPYQKSLYISFPO-UHFFFAOYSA-N   
3  XTUPUYCJWKHGSW-UHFFFAOYSA-L   
4  FAUAZXVRLVIARB-UHFFFAOYSA-N   

                                              SMILES  Solubility   SD  \
0                [Br-].CCCCCCCCCCCCCCCCCC[N+](C)(C)C   -3.616127  0.0   
1                               O=C1Nc2cccc3cccc1c23   -3.254767  0.0   
2                                    Clc1ccc(C=O)cc1   -2.177078  0.0   
3  [Zn++].CC(c1ccccc1)c2cc(C(C)c3ccccc3)c(O)c(c2)...   -3.924409  0.0   
4  C1OC1CN(CC2CO2)c3ccc(Cc4ccc(cc4)N(CC5CO5)CC6CO...   -4.662065  0.0   

   Ocurrences Group    MolWt  ...  NumAromaticRings  NumSaturatedRings  \
0           1    G1  392.510  ...               0.0                0.0   
1           1    G1  169.183  ...               2.0                0.0   
2           1    G1  140.569  ...               1.0                0.0   
3           1    G1  756.226  ...               6.0                0.0   
4           1    G1  422.525  ...               2.0                4.0   

   NumAliphaticRings  RingCount    TPSA   LabuteASA      BalabanJ  \
0                0.0        0.0    0.00  158.520601  0.000000e+00   
1                1.0        3.0   29.10   75.183563  2.582996e+00   
2                0.0        1.0   17.07   58.261134  3.009782e+00   
3                0.0        6.0  120.72  323.755434  2.322963e-07   
4                4.0        6.0   56.60  183.183268  1.084427e+00   

       BertzCT                                 active ingredient  \
0   210.377334                     CCCCCCCCCCCCCCCCCC[N+](C)(C)C   
1   511.229248                                               NaN   
2   202.661065                                               NaN   
3  1964.648666  CC(c1ccccc1)c1cc(C(=O)[O-])c(O)c(C(C)c2ccccc2)c1   
4   769.899934                                               NaN   

                                                salt  
0                                              [Br-]  
1                                                NaN  
2                                                NaN  
3  [Zn+2].CC(c1ccccc1)c1cc(C(=O)[O-])c(O)c(C(C)c2...  
4                                                NaN  

[5 rows x 28 columns]

In [5]:
# inorganic molecule을 제거하는 이유:
# 1. RDKit으로 분자 구조를 읽을 때 문제가 발생하는 경우가 있음
# 2. 신약 개발 시 무기분자는 원하는 구조가 아니기 때문에 제외함
#    organic molecule은 탄소와 수소가 주 골격을 이루는 구조이며,
#    그렇지 않은 경우는 무기분자로 간주함
# 첫 번째 방법은 탄소가 없는 분자를 찾는 것임

column_key = 'active ingredient'  # 유효 성분이 저장된 컬럼명

# 탄소 원소가 없는 화합물을 선택하기 위해 탄소 원소 리스트 정의
carbon = ['C']
c_index = []  # 탄소가 없는 화합물의 인덱스를 저장할 리스트

for index, row in df.iterrows():  # 데이터프레임의 각 행을 순회
    try:
        m = Chem.MolFromSmiles(row[column_key])  # 스마일코드를 분자 구조로 변환
        flag = 0  # 탄소 원소 여부를 나타내는 플래그

        for atom in m.GetAtoms():  # 분자의 각 원자를 순회
            if atom.GetSymbol() in carbon:  # 원자가 탄소(C)인 경우
                flag = 1  # 플래그를 1로 설정하고 루프 종료
                break

        if flag == 0:  # 플래그가 0인 경우 (즉, 탄소가 없는 분자)
            c_index.append(index)  # 인덱스를 리스트에 추가

    except Exception as e:
        # 예외 발생 시 인덱스와 행 정보를 출력하고 인덱스를 리스트에 추가
        print(index, row, str(e))
        c_index.append(index)

# c_index에는 탄소가 없는 화합물의 인덱스가 저장됨

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumAromaticRings                                                     2.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            2.0
TPSA                                                               33.12
LabuteASA                                                      64.126949
BalabanJ                                                        2.913161
BertzCT                                                       378.724446
active ingredient                                                    NaN
salt                                                                 NaN
Name: 279, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
282 ID                    

[07:32:58] WARNING: not removing hydrogen atom without neighbors


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            0.0
TPSA                                                                52.6
LabuteASA                                                     158.346396
BalabanJ                                                        3.790205
BertzCT                                                       314.587855
active ingredient                                                    NaN
salt                                                                 NaN
Name: 1408, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
1409 ID                  

[07:33:00] WARNING: not removing hydrogen atom without neighbors
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumSaturatedRings                                                 0.0
NumAliphaticRings                                                 0.0
RingCount                                                         1.0
TPSA                                                            60.69
LabuteASA                                                   51.814104
BalabanJ                                                     3.247835
BertzCT                                                       199.293
active ingredient                                                 NaN
salt                                                              NaN
Name: 3855, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
3856 ID                                                            B-320
Name                                               h

...

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumSaturatedRings                                                    2.0
NumAliphaticRings                                                    2.0
RingCount                                                            3.0
TPSA                                                               93.14
LabuteASA                                                      147.42019
BalabanJ                                                        1.685618
BertzCT                                                       693.108074
active ingredient                                                    NaN
salt                                                                 NaN
Name: 5285, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
5286 ID                                                                B-2133
Name                

[07:33:07] WARNING: not removing hydrogen atom without neighbors


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                122.0
NumAromaticRings                                                     2.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    2.0
RingCount                                                            4.0
TPSA                                                               87.74
LabuteASA                                                     141.287552
BalabanJ                                                        2.219376
BertzCT                                                       1156.26489
active ingredient                                                    NaN
salt                                                                 NaN
Name: 8461, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<w

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                 76.0
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    1.0
NumAliphaticRings                                                    2.0
RingCount                                                            2.0
TPSA                                                               44.76
LabuteASA                                                      82.135019
BalabanJ                                                        2.373787
BertzCT                                                       316.083688
active ingredient                                                    NaN
salt                                                                 NaN
Name: 9809, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<w

In [6]:
# 수소 원소가 없는 화합물을 선택하기 위해 수소 원소 리스트 정의
hydrogen = ['H']
h_index = []  # 수소가 없는 화합물의 인덱스를 저장할 리스트

for index, row in df.iterrows():  # 데이터프레임의 각 행을 순회
    try:
        m = Chem.MolFromSmiles(row[column_key])  # 스마일코드를 분자 구조로 변환
        mH = Chem.AddHs(m)  # 분자 구조에 수소 원자를 추가
        flag = 0  # 수소 원소 여부를 나타내는 플래그

        for atom in mH.GetAtoms():  # 분자의 각 원자를 순회
            if atom.GetSymbol() in hydrogen:  # 원자가 수소(H)인 경우
                flag = 1  # 플래그를 1로 설정하고 루프 종료
                break

        if flag == 0:  # 플래그가 0인 경우 (즉, 수소가 없는 분자)
            h_index.append(index)  # 인덱스를 리스트에 추가

    except Exception as e:
        # 예외 발생 시 인덱스와 행 정보를 출력하고 인덱스를 리스트에 추가
        print(index, row, str(e))
        h_index.append(index)

# h_index에는 수소가 없는 화합물의 인덱스가 저장됨

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                 54.0
NumAromaticRings                                                     1.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            1.0
TPSA                                                               50.44
LabuteASA                                                       57.92186
BalabanJ                                                        3.278727
BertzCT                                                       274.424863
active ingredient                                                    NaN
salt                                                                 NaN
Name: 147, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wc

[07:33:18] WARNING: not removing hydrogen atom without neighbors


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                236.0
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    2.0
NumAliphaticRings                                                    2.0
RingCount                                                            2.0
TPSA                                                              129.26
LabuteASA                                                     245.875846
BalabanJ                                                        1.871876
BertzCT                                                       770.935498
active ingredient                                                    NaN
salt                                                                 NaN
Name: 1397, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<w

[07:33:21] WARNING: not removing hydrogen atom without neighbors
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    1.0
NumAliphaticRings                                                    1.0
RingCount                                                            1.0
TPSA                                                               18.46
LabuteASA                                                      56.150163
BalabanJ                                                         2.11279
BertzCT                                                        74.985336
active ingredient                                                    NaN
salt                                                                 NaN
Name: 5355, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
5356 ID                  

...

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumAromaticRings                                                     5.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            5.0
TPSA                                                                 0.0
LabuteASA                                                     116.137086
BalabanJ                                                        2.317611
BertzCT                                                        917.00497
active ingredient                                                    NaN
salt                                                                 NaN
Name: 7563, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<wchar_t> > from this Python object of type float
7564 ID                  

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                 94.0
NumAromaticRings                                                     1.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            1.0
TPSA                                                               49.33
LabuteASA                                                     102.810597
BalabanJ                                                        3.185586
BertzCT                                                       342.499659
active ingredient                                                    NaN
salt                                                                 NaN
Name: 9189, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<w

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                 76.0
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    1.0
NumAliphaticRings                                                    2.0
RingCount                                                            2.0
TPSA                                                               44.76
LabuteASA                                                      82.135019
BalabanJ                                                        2.373787
BertzCT                                                       316.083688
active ingredient                                                    NaN
salt                                                                 NaN
Name: 9809, dtype: object No registered converter was able to produce a C++ rvalue of type std::basic_string<wchar_t, std::char_traits<wchar_t>, std::allocator<w

In [7]:
# 금속 원소를 포함한 화합물을 선택하기 위한 인덱스 리스트
metal_index = []

# 보통 신약 개발에 사용되는 유기 원소 리스트 정의
organic = ['H', 'C', 'N', 'O', 'F', 'P', 'S', 'Cl', 'Br', 'I', 'Na', 'K', 'Si']

for index, row in df.iterrows():  # 데이터프레임의 각 행을 순회
    try:
        m = Chem.MolFromSmiles(row[column_key])  # 스마일코드를 분자 구조로 변환

        for atom in m.GetAtoms():  # 분자의 각 원자를 순회
            if atom.GetSymbol() not in organic:  # 원자가 유기 원소 리스트에 없는 경우
                metal_index.append(index)  # 금속을 포함한 화합물의 인덱스를 리스트에 추가
                break  # 금속 원소를 발견하면 루프 종료

    except:
        # 예외 발생 시 인덱스와 행 정보를 출력하고 인덱스를 리스트에 추가
        print(index, row)

# metal_index에는 금속 원소를 포함한 화합물의 인덱스가 저장됨

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                                 64.0
NumAromaticRings                                                     0.0
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            0.0
TPSA                                                                26.3
LabuteASA                                                      61.646032
BalabanJ                                                        3.726387
BertzCT                                                       171.156434
active ingredient                                                    NaN
salt                                                                 NaN
Name: 154, dtype: object
155 ID                                                             A-259
Name                                 bismuth hydroxide nitrate 

[07:39:06] WARNING: not removing hydrogen atom without neighbors


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            0.0
TPSA                                                                9.23
LabuteASA                                                       83.86716
BalabanJ                                                         2.75815
BertzCT                                                        71.193662
active ingredient                                                    NaN
salt                                                                 NaN
Name: 1460, dtype: object
1461 ID                                                                A-2511
Name                   3-[[2-(2-cyanoethoxy)ethyl][4-[(4-nitrophenyl)...
InChI                  InChI=1S/C20H20N6O3/c21-11-1-13-25(14-16-29-15...
InChIKey                                     PNWYPUYECVEC

[07:39:08] WARNING: not removing hydrogen atom without neighbors
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumSaturatedRings                                             0.0
NumAliphaticRings                                             0.0
RingCount                                                     0.0
TPSA                                                          0.0
LabuteASA                                               38.989144
BalabanJ                                                 2.539539
BertzCT                                                  17.60964
active ingredient                                             NaN
salt                                                          NaN
Name: 4359, dtype: object
4360 ID                                                       B-1052
Name                                 2,3-dimethyl-1,3-butadiene
InChI                  InChI=1S/C6H10/c1-5(2)6(3)4/h1,3H2,2,4H3
InChIKey                            SDJHPPZKZZWAKF-UHFFFAOYSA-N
SMILES                                             CC(=C)C(C)=C
Solubility         

...

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumSaturatedRings                                                    0.0
NumAliphaticRings                                                    0.0
RingCount                                                            2.0
TPSA                                                               72.55
LabuteASA                                                      98.262631
BalabanJ                                                        2.206265
BertzCT                                                       537.615768
active ingredient                                                    NaN
salt                                                                 NaN
Name: 7137, dtype: object
7138 ID                                                                B-4553
Name                                              methyl p-aminobenzoate
InChI                  InChI=1S/C8H9NO2/c1-11-8(10)6-2-4-7(9)5-3-6/h2...
InChIKey                                     LZXXNPOYQCLX

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
NumValenceElectrons                                              44.0
NumAromaticRings                                                  0.0
NumSaturatedRings                                                 0.0
NumAliphaticRings                                                 0.0
RingCount                                                         0.0
TPSA                                                            20.23
LabuteASA                                                   45.358195
BalabanJ                                                     3.360435
BertzCT                                                     42.141709
active ingredient                                                 NaN
salt                                                              NaN
Name: 8719, dtype: object
8720 ID                                                                E-241
Name                                                  2-ethyl-1-butanol
InChI              

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



9860 ID                                                                G-1066
Name                                                             Sucrose
InChI                  InChI=1S/C12H22O11/c13-1-4-6(16)8(18)9(19)11(2...
InChIKey                                     CZMRCDWAGMRECN-UHFFFAOYSA-N
SMILES                          OCC2OC(OC1(CO)OC(CO)C(O)C1O)C(O)C(O)C2O 
Solubility                                                          0.79
SD                                                                   0.0
Ocurrences                                                             1
Group                                                                 G1
MolWt                                                            342.297
MolLogP                                                          -5.3956
MolMR                                                            68.6414
HeavyAtomCount                                                      23.0
NumHAcceptors                                 

In [8]:
total_index = c_index + h_index + metal_index
total_index = list(set(total_index))

df_inorga = df.loc[total_index, :]
df_inorga.to_csv("/content/drive/MyDrive/파이널/data/aqsol_inorganic.csv", index=False)

df_orga = df.drop(total_index)
df_orga.to_csv("/content/drive/MyDrive/파이널/data/aqsol_organic.csv", index=False)